In [2]:
from matplotlib import pyplot as plt
from matplotlib.colors import LinearSegmentedColormap
import seaborn as sns
import plotly.express as px

In [3]:
import numpy as np
import pandas as pd

In [4]:
import pulp

In [5]:
f_conv_mon = 0.0008*1000

In [6]:
C = np.array([[105, 1267, 1134, 2758, 515, 1350, 1311, 1750, 1565, 1137, 3110, 1365]]) #dinar

C = C * f_conv_mon

#C = np.concatenate((C[:, 0:1], C[:, 2:4], C[:, 5:11]), axis=1)

C = np.concatenate((C, C), axis=1)


In [7]:
C = np.concatenate(( np.concatenate((C, np.zeros(C.shape)), axis=1), 
                     np.concatenate((np.zeros((1, 24)), np.ones((1, 24))), axis=1),
                     np.concatenate((np.ones((1, 24)), np.zeros((1, 24))), axis=1)
                    ), axis=0)

In [8]:
A = np.array([  [     1,       1,       1,       1,       1,       1,       0,       0,       0,       0,       0,       0],
                [     0,       0,       0,       0,       0,       0,       1,       1,       1,       1,       1,       1],
                [   100,      50,      50,      50,     100,     100,      50,     100,     100,     100,     100,     100],
                [   100,      50,      50,      25,      50,     150,      50,     100,     100,      50,      50,      50],
                [     0,       0,       0,       0,       0,      12,       0,       0,      12,       0,       0,       0],
                [     1,       1,       2,       1,       1,       3,       1,       2,       2,       2,       3,       1],
                [     6,      29,      32,      14,      54,      60,       0,       0,      18,      13,      29,       8],
                [     2,       0,      17,      23,       0,       0,      22,       6,      50,     102,      77,      31],
                [     0,       0,       0,       0,       0,      12,      35,      24,      80,       0,     112,      58],
                [     9,       8,       7,      34,      26,      22,       0,       0,      52,       0,      43,       0],
                [   1.5,     1.5,     1.5,     1.5,     1.5,     1.5,     1.5,     1.5,     1.5,     1.5,     1.5,     1.5],
                [     1,       1,       1,       1,       1,       1,       1,       1,       1,       1,       1,       1],
                [   0.5,     0.5,     0.5,     0.5,     0.5,     0.5,     0.5,     0.5,     0.5,     0.5,     0.5,     0.5],
                [   0.5,       0,       0,       0,       0,       0,       0,       0,       0,       0,       0,       0],
                [   390,     355,     370,     430,     440,       0,     275,       0,     100,     133,     213,     100],
                [   275,       0,     470,     305,       0,       0,    1430,     188,    1015,     955,    1343,    1215],
                [     0,       0,     150,       0,       0,     750,     443,     840,    1683,       0,    1748,    1095],
                [   300,     295,     305,     303,     210,     860,       0,       0,       0,       0,       0,       0],
                [345000,  233000,  216000,  242000,  360000,  650000,  244000,  242000,  310000,  263000,  250000,  285000]])

In [9]:
b = np.array([2395,2260,419190,397560,7000,13075,50593,554800,562400,562400,103056,103056,103056,954,20699716,20929709,21159705,21159705,1445855000]) #dinar

In [10]:
b[18] = b[18] * f_conv_mon
A[18,:] = A[18,:] * f_conv_mon

In [11]:
A = np.concatenate((np.concatenate((A, np.zeros(A.shape)), axis=1), 
                    np.concatenate((np.zeros(A.shape), A), axis=1)))

In [12]:
A.shape

(38, 24)

In [13]:
nX = 12
_A = np.zeros((2, A.shape[1]))
_A[0, 0] = _A[1, 2] = _A[1, 3] =  -1
_A[0, nX+2] = _A[0, nX+3] = _A[1, nX+7] = 1

In [14]:
A = np.concatenate((A, _A), axis=0)

In [15]:
b = np.concatenate((b, b, np.array([0, 0])), axis=0)

In [16]:
A = np.concatenate((A, np.zeros(A.shape)), axis=1)

In [17]:
A.shape

(40, 48)

In [18]:
I = np.identity(24)
w1 = 113 # min 5%
w2 = -(10**10)

A = np.concatenate((A, np.concatenate((-I, w1*I), axis=1), np.concatenate((I, w2*I), axis=1)), axis=0)

In [19]:
A.shape

(88, 48)

In [20]:
b = np.concatenate((b, np.zeros((A.shape[0] - b.shape[0]))), axis=0)

In [21]:
I = np.identity(12)
_A = np.concatenate((I, I), axis=1)
_A = np.concatenate((_A, np.zeros((_A.shape[0], A.shape[1] - _A.shape[1]))), axis=1)
#A = np.concatenate((A, _A), axis=0)

In [22]:
#b = np.concatenate((b, np.ones((6,))*2395, np.ones((6,))*2260), axis=0)

In [23]:
sig = lambda sigma, NUM_ITER: 1/(1 + np.exp(sigma*(np.linspace(0, NUM_ITER, NUM_ITER)-(NUM_ITER/2))))

alpha_lin = np.linspace(0, 1, 1000)
alpha_sig_004 = sig(-0.004, 1000)
alpha_sig_06 = sig(-0.06, 1000)

In [24]:
l_alpha = {'alpha_lin':     alpha_lin, 
           #'alpha_sig_004': alpha_sig_004, 
           #'alpha_sig_06':  alpha_sig_06,
           }

In [25]:
def create_var():
    var = np.array([])

    lbx = [0] * 24
    lbx[0] = 1500
    lbx[12] = 1500

    for j in range(1, 3):
        for i in range(1, 13):
            var = np.append(var, np.array([pulp.LpVariable("x_{}_{:02d}".format(j, i), lowBound = lbx[i-1], upBound=None, cat='Integer')]))

    for j in range(1, 3):
        for i in range(1, 13):
            var = np.append(var, np.array([pulp.LpVariable("y_{}_{:02d}".format(j, i), cat='Binary')]))
    
    return var

In [26]:
z1p = 12559922.4
z1n = 252000

_z1 = z1p-z1n

z2p = 24
z2n = 2

_z2 = z2p-z2n

z3p = 9310.0
z3n = 3000.0

_z3 = z3p-z3n

In [27]:
def objective(alpha):
    var = create_var()

    Fs = np.array([])

    for c in C:
        Fs = np.append(Fs, c.dot(var))

    fo = alpha*((Fs[0] - z1n)/_z1) + (1 - alpha) * ((Fs[1] -z2n)/(_z2*2) + (Fs[2] - z3n)/(_z3*2))

    return (var, Fs, fo)

In [28]:
def print_solution(sol, linearProblem, X):
    saida = "\nStatus = {} \nValue = {}".format(pulp.LpStatus[sol], pulp.value(linearProblem.objective))
    
    for i in range(0, X.shape[0]):
        saida += "\n{} = {}".format(X[i], pulp.value(X[i]))
    
    print(saida)

In [29]:
columns=["alpha_type", "iter", "alpha", "status"]
for j in range(1, 3):
        for i in range(1, 13):
            columns.append("X_{}_{}".format(j, i))
for j in range(1, 3):
        for i in range(1, 13):
            columns.append("Y_{}_{}".format(j, i))
columns = columns + ["obj_value", "f1", "f2", "f3"]

In [30]:
solution_lst = []
for key in l_alpha:
    aph = l_alpha[key]
    for i_alpha in range(0, len(aph)):            
        alpha = aph[i_alpha]
        d_var, F, f = objective(alpha)
        model = pulp.LpProblem("First_Model", pulp.LpMaximize)
        #model = pulp.LpProblem("First_Model", pulp.LpMinimize)

        model += f 

        Ax = A.dot(d_var)

        for i in range(0, Ax.shape[0]):
            model += Ax[i] <= b[i]
        
        solution = model.solve(pulp.GLPK())
        #solution = model.solve()

        X = np.array([pulp.value(i) for i in d_var])

        fs = C.dot(X)

        solution_lst.append([key,
                            i_alpha,
                            alpha,
                            str(pulp.LpStatus[solution])] +
                            X.tolist() +
                            [pulp.value(model.objective),
                            fs[0],
                            fs[1],
                            fs[2],
                            ])

    #print_solution(sol=solution, linearProblem=model, X=d_var)

GLPSOL--GLPK LP/MIP Solver 5.0
Parameter(s) specified in the command line:
 --cpxlp /tmp/12e22a043b3f4aadacef0bbf918ba059-pulp.lp -o /tmp/12e22a043b3f4aadacef0bbf918ba059-pulp.sol
Reading problem data from '/tmp/12e22a043b3f4aadacef0bbf918ba059-pulp.lp'...
88 rows, 48 columns, 430 non-zeros
48 integer variables, 24 of which are binary
227 lines were read
GLPK Integer Optimizer 5.0
88 rows, 48 columns, 430 non-zeros
48 integer variables, 24 of which are binary
Preprocessing...
24 constraint coefficient(s) were reduced
64 rows, 48 columns, 242 non-zeros
48 integer variables, 24 of which are binary
Scaling...
 A: min|aij| =  1.000e+00  max|aij| =  5.200e+05  ratio =  5.200e+05
GM: min|aij| =  4.553e-01  max|aij| =  2.196e+00  ratio =  4.824e+00
EQ: min|aij| =  2.075e-01  max|aij| =  1.000e+00  ratio =  4.820e+00
2N: min|aij| =  1.250e-01  max|aij| =  1.500e+00  ratio =  1.200e+01
Constructing initial basis...
Size of triangular part is 64
Solving LP relaxation...
GLPK Simplex Optimizer 5.

In [31]:
dt_all = pd.DataFrame(solution_lst, columns=columns)

In [32]:
#from unicodedata import decimal
#df = pd.DataFrame(b.transpose())
#df.to_clipboard(index=False,header=False, decimal=',')

In [33]:
dt = dt_all[dt_all.alpha_type == 'alpha_lin']

In [34]:
#sns.scatterplot(data=dt, x = 'alpha', y='obj_value')

fig = px.scatter(dt, 
              x ='alpha', 
              y='obj_value', 
              #title='Função Objetivo (g) versus λ',
              #title='Objective Function (z<sub>2y</sub>) versus λ',
              #color='alpha_type',
              labels={'alpha': 'λ',
                      'obj_value': 'g'})
                      
fig.update_traces(marker=dict(color='rgb(115, 115, 115)',
                              size=3
                              )
                    )

fig.update_layout(
    xaxis=dict(
        showline=True,
        showgrid=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    yaxis=dict(
        showgrid=True,
        zeroline=False,
        showline=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    autosize=False,
    margin=dict(
        autoexpand=True,
        l=100,
        r=20,
        t=110,
    ),
    showlegend=True,
    plot_bgcolor='white'
)
#fig['data'][0]['line']['color']='rgb(115, 115, 115)'
#fig['data'][0]['line']['width']=3

fig.show()
fig.write_image('images/fig_mdl2_z2y_vs_lambda.svg')

In [35]:
import tikzplotly

tikzplotly.save("figure.tex", fig)

In [36]:
#sns.lineplot(data=dt, x = 'alpha', y='f1')

#sns.lineplot(data=dt, x = 'alpha', y='f2')

#sns.lineplot(data=dt, x = 'alpha', y='f3')

fig = px.scatter(dt, 
              x ='alpha', 
              y='f1', 
              #title='Net Income of Farm (z<sub>2y,1</sub>) versus λ',
              #title='Retorno Líquido da Fazenda (g<sub>1</sub>) versus λ',
              #color='alpha_type',
              labels={'alpha': 'λ',
                      #'alpha_type': 'λ',
                      'f1': 'g<sub>1</sub> (USD)'})

fig.update_traces(marker=dict(color='rgb(115, 115, 115)',
                              size=3
                              )
                    )

fig.update_layout(
    xaxis=dict(
        showline=True,
        showgrid=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    yaxis=dict(
        showgrid=False,
        zeroline=False,
        showline=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        dtick=500000,
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    autosize=False,
    margin=dict(
        autoexpand=True,
        l=100,
        r=20,
        t=110,
    ),
    showlegend=True,
    plot_bgcolor='white'
)
fig['data'][0]['line']['color']='rgb(115, 115, 115)'
fig['data'][0]['line']['width']=3

fig.show()
fig.write_image('images/fig_mdl2_z2y1_vs_lambda.svg')

In [37]:
import tikzplotly

tikzplotly.save("figure.tex", fig)

In [38]:
#sns.lineplot(data=dt, x = 'alpha', y='f2')

#sns.lineplot(data=dt, x = 'alpha', y='f3')

fig = px.scatter(dt, 
              x ='alpha', 
              y='f2', 
              #title='Number of Different Crops Grown (z<sub>2y,2</sub>) versus λ',
              #title='Número de Diferentes Culturas Plantadas (g<sub>2</sub>) versus λ',
              #color='alpha_type',
              labels={'alpha': 'λ',
                      'f2': 'g<sub>2</sub>'})

fig.update_traces(marker=dict(color='rgb(115, 115, 115)',
                              size=3
                              )
                    )

fig.update_layout(
    xaxis=dict(
        showline=True,
        showgrid=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    yaxis=dict(
        showgrid=True,
        zeroline=False,
        showline=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    autosize=False,
    margin=dict(
        autoexpand=True,
        l=100,
        r=20,
        t=110,
    ),
    showlegend=True,
    plot_bgcolor='white'
)
fig['data'][0]['line']['color']='rgb(115, 115, 115)'
fig['data'][0]['line']['width']=3

fig.show()
fig.write_image('images/fig_mdl2_z2y2_vs_lambda.svg')

In [39]:
import tikzplotly

tikzplotly.save("figure.tex", fig)

In [36]:
#sns.lineplot(data=dt, x = 'alpha', y='f3')

fig = px.scatter(dt, 
              x ='alpha', 
              y='f3', 
              #title='Used Area (z<sub>2y,3</sub>) versus λ',
              #title='Área Usada (g<sub>3</sub>) versus λ',
              #color='alpha_type',
              labels={'alpha': 'λ',
                      'f3': 'g<sub>3</sub>'})

fig.update_traces(marker=dict(color='rgb(115, 115, 115)',
                              size=3
                              )
                    )

fig.update_layout(
    xaxis=dict(
        showline=True,
        showgrid=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    yaxis=dict(
        showgrid=True,
        zeroline=False,
        showline=False,
        showticklabels=True,
        linecolor='rgb(204, 204, 204)',
        linewidth=2,
        ticks='outside',
        tickfont=dict(
            family='Arial',
            size=12,
            color='rgb(82, 82, 82)',
        ),
    ),
    autosize=False,
    margin=dict(
        autoexpand=True,
        l=100,
        r=20,
        t=110,
    ),
    showlegend=True,
    plot_bgcolor='white'
)
fig['data'][0]['line']['color']='rgb(115, 115, 115)'
fig['data'][0]['line']['width']=3

fig.show()
fig.write_image('images/fig_mdl2_z2y3_vs_lambda.svg')

In [37]:
#cm = color_continuous_scale=px.colors.diverging.Tealrose,
cm = ['rgb(77,77,77)', 'rgb(153, 153, 153)', 'rgb(186,186,186)', 'rgb(244,165,130)', 'rgb(214,96,77)','rgb(230, 39, 23)']
cm = ['rgb(77,77,77)', 'rgb(153, 153, 153)', 'rgb(214,96,77)','rgb(230, 39, 23)']

In [39]:
dt

alpha_type  iter     alpha   status  X_1_1  X_1_2  X_1_3  X_1_4  X_1_5  \
0    alpha_lin     0  0.000000  Optimal   1500    443    113    113    113   
1    alpha_lin     1  0.001001  Optimal   1500    113    113    443    113   
2    alpha_lin     2  0.002002  Optimal   1500    113    113    443    113   
3    alpha_lin     3  0.003003  Optimal   1500    113    113    443    113   
4    alpha_lin     4  0.004004  Optimal   1500    113    113    443    113   
..         ...   ...       ...      ...    ...    ...    ...    ...    ...   
995  alpha_lin   995  0.995996  Optimal   1500      0      0    895      0   
996  alpha_lin   996  0.996997  Optimal   1500      0      0    895      0   
997  alpha_lin   997  0.997998  Optimal   1500      0      0    895      0   
998  alpha_lin   998  0.998999  Optimal   1500      0      0    895      0   
999  alpha_lin   999  1.000000  Optimal   1500      0      0    895      0   

     X_1_6  ...  Y_2_7  Y_2_8  Y_2_9  Y_2_10  Y_2_11  Y_2_12  obj_value  \
0      113  ...      1      1      1       1       1       1   1.000000   
1      113  ...      1      1      1       1       1       1   0.999751   
2      113  ...      1      1      1       1       1       1   0.999502   
3      113  ...      1      1      1       1       1       1   0.999253   
4      113  ...      1      1      1       1       1       1   0.999004   
..     ...  ...    ...    ...    ...     ...     ...     ...        ...   
995      0  ...      1      1      0       0       1       0   0.998630   
996      0  ...      1      1      0       0       1       0   0.998972   
997      0  ...      1      1      0       0       1       0   0.999315   
998      0  ...      1      1      0       0       1       0   0.999657   
999      0  ...      1      1      0       0       1       0   1.000000   

             f1    f2      f3  
0     7360348.8  24.0  9310.0  
1     9497513.6  24.0  9310.0  
2     9497513.6  24.0  9310.0  
3     9497821.6  24.0  9310.0  
4     9497821.6  24.0  9310.0  
..          ...   ...     ...  
995  12559922.4   9.0  9294.0  
996  12559922.4   9.0  9294.0  
997  12559922.4   9.0  9294.0  
998  12559922.4   9.0  9294.0  
999  12559922.4   9.0  9294.0  

[1000 rows x 56 columns]

In [38]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_1', 'X_1_2', 'X_1_3', 'X_1_4', 'X_1_5', 'X_1_6', 
                                         'X_1_7', 'X_1_8', 'X_1_9', 'X_1_10', 'X_1_11', 'X_1_12'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_1_1':'u<sub>1</sub>', 
                                        'X_1_2':'u<sub>2</sub>', 
                                        'X_1_3':'u<sub>3</sub>', 
                                        'X_1_4':'u<sub>4</sub>', 
                                        'X_1_5':'u<sub>5</sub>', 
                                        'X_1_6':'u<sub>6</sub>', 
                                        'X_1_7':'u<sub>7</sub>', 
                                        'X_1_8':'u<sub>8</sub>', 
                                        'X_1_9':'u<sub>9</sub>', 
                                        'X_1_10':'u<sub>10</sub>', 
                                        'X_1_11':'u<sub>11</sub>', 
                                        'X_1_12':'u<sub>12</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1.svg', width=1100, height=650)

AttributeError: 'DataFrame' object has no attribute 'iteritems'

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_2', 'X_1_4', 'X_1_7', 'X_1_8', 'X_1_11', 'X_1_12'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_1_1':'u<sub>1</sub>', 
                                        'X_1_2':'u<sub>2</sub>', 
                                        'X_1_3':'u<sub>3</sub>', 
                                        'X_1_4':'u<sub>4</sub>', 
                                        'X_1_5':'u<sub>5</sub>', 
                                        'X_1_6':'u<sub>6</sub>', 
                                        'X_1_7':'u<sub>7</sub>', 
                                        'X_1_8':'u<sub>8</sub>', 
                                        'X_1_9':'u<sub>9</sub>', 
                                        'X_1_10':'u<sub>10</sub>', 
                                        'X_1_11':'u<sub>11</sub>', 
                                        'X_1_12':'u<sub>12</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1_redu.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_1', 'X_1_2', 'X_1_3', 'X_1_4', 'X_1_5', 'X_1_6'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_1_1':'u<sub>1</sub>', 
                                        'X_1_2':'u<sub>2</sub>', 
                                        'X_1_3':'u<sub>3</sub>', 
                                        'X_1_4':'u<sub>4</sub>', 
                                        'X_1_5':'u<sub>5</sub>', 
                                        'X_1_6':'u<sub>6</sub>', 
                                        'X_1_7':'u<sub>7</sub>', 
                                        'X_1_8':'u<sub>8</sub>', 
                                        'X_1_9':'u<sub>9</sub>', 
                                        'X_1_10':'u<sub>10</sub>', 
                                        'X_1_11':'u<sub>11</sub>', 
                                        'X_1_12':'u<sub>12</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1_redu_summer.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_7', 'X_1_8', 'X_1_9', 'X_1_10', 'X_1_11', 'X_1_12'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_1_1':'u<sub>1</sub>', 
                                        'X_1_2':'u<sub>2</sub>', 
                                        'X_1_3':'u<sub>3</sub>', 
                                        'X_1_4':'u<sub>4</sub>', 
                                        'X_1_5':'u<sub>5</sub>', 
                                        'X_1_6':'u<sub>6</sub>', 
                                        'X_1_7':'u<sub>7</sub>', 
                                        'X_1_8':'u<sub>8</sub>', 
                                        'X_1_9':'u<sub>9</sub>', 
                                        'X_1_10':'u<sub>10</sub>', 
                                        'X_1_11':'u<sub>11</sub>', 
                                        'X_1_12':'u<sub>12</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_1_redu_winter.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_1', 'X_2_2', 'X_2_3', 'X_2_4', 'X_2_5', 'X_2_6', 
                                         'X_2_7', 'X_2_8', 'X_2_9', 'X_2_10', 'X_2_11', 'X_2_12'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2.svg', width=1100, height=650)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_2', 'X_2_4', 'X_2_7', 'X_2_8', 'X_2_9',  'X_2_11', 'X_2_12'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2_redu.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_1', 'X_2_2', 'X_2_3', 'X_2_4', 'X_2_5', 'X_2_6'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2_redu_summer.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_1', 'X_2_2', 'X_2_3', 'X_2_4', 'X_2_5', 'X_2_6'],
                             color="f1", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f1': 'g<sub>1</sub> (USD)',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f1.min(), dt.f1.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y1_2_redu_winter.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_1', 'X_1_2', 'X_1_3', 'X_1_4', 'X_1_5', 'X_1_6', 
                                         'X_1_7', 'X_1_8', 'X_1_9', 'X_1_10', 'X_1_11', 'X_1_12'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_1_1':'u<sub>1,1</sub>', 
                                        'X_1_2':'u<sub>2,1</sub>', 
                                        'X_1_3':'u<sub>3,1</sub>', 
                                        'X_1_4':'u<sub>4,1</sub>', 
                                        'X_1_5':'u<sub>5,1</sub>', 
                                        'X_1_6':'u<sub>6,1</sub>', 
                                        'X_1_7':'u<sub>7,1</sub>', 
                                        'X_1_8':'u<sub>8,1</sub>', 
                                        'X_1_9':'u<sub>9,1</sub>', 
                                        'X_1_10':'u<sub>10,1</sub>', 
                                        'X_1_11':'u<sub>11,1</sub>', 
                                        'X_1_12':'u<sub>12,1</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1.svg', width=1100, height=650)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_2', 'X_1_4', 'X_1_7', 'X_1_8', 'X_1_11', 'X_1_12'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_1_1':'u<sub>1,1</sub>', 
                                        'X_1_2':'u<sub>2,1</sub>', 
                                        'X_1_3':'u<sub>3,1</sub>', 
                                        'X_1_4':'u<sub>4,1</sub>', 
                                        'X_1_5':'u<sub>5,1</sub>', 
                                        'X_1_6':'u<sub>6,1</sub>', 
                                        'X_1_7':'u<sub>7,1</sub>', 
                                        'X_1_8':'u<sub>8,1</sub>', 
                                        'X_1_9':'u<sub>9,1</sub>', 
                                        'X_1_10':'u<sub>10,1</sub>', 
                                        'X_1_11':'u<sub>11,1</sub>', 
                                        'X_1_12':'u<sub>12,1</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1_redu.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_1', 'X_1_2', 'X_1_3', 'X_1_4', 'X_1_5', 'X_1_6'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_1_1':'u<sub>1,1</sub>', 
                                        'X_1_2':'u<sub>2,1</sub>', 
                                        'X_1_3':'u<sub>3,1</sub>', 
                                        'X_1_4':'u<sub>4,1</sub>', 
                                        'X_1_5':'u<sub>5,1</sub>', 
                                        'X_1_6':'u<sub>6,1</sub>', 
                                        'X_1_7':'u<sub>7,1</sub>', 
                                        'X_1_8':'u<sub>8,1</sub>', 
                                        'X_1_9':'u<sub>9,1</sub>', 
                                        'X_1_10':'u<sub>10,1</sub>', 
                                        'X_1_11':'u<sub>11,1</sub>', 
                                        'X_1_12':'u<sub>12,1</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1_redu_summer.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_1_7', 'X_1_8', 'X_1_9', 'X_1_10', 'X_1_11', 'X_1_12'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_1_1':'u<sub>1,1</sub>', 
                                        'X_1_2':'u<sub>2,1</sub>', 
                                        'X_1_3':'u<sub>3,1</sub>', 
                                        'X_1_4':'u<sub>4,1</sub>', 
                                        'X_1_5':'u<sub>5,1</sub>', 
                                        'X_1_6':'u<sub>6,1</sub>', 
                                        'X_1_7':'u<sub>7,1</sub>', 
                                        'X_1_8':'u<sub>8,1</sub>', 
                                        'X_1_9':'u<sub>9,1</sub>', 
                                        'X_1_10':'u<sub>10,1</sub>', 
                                        'X_1_11':'u<sub>11,1</sub>', 
                                        'X_1_12':'u<sub>12,1</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_1_redu_winter.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_1', 'X_2_2', 'X_2_3', 'X_2_4', 'X_2_5', 'X_2_6', 
                                         'X_2_7', 'X_2_8', 'X_2_9', 'X_2_10', 'X_2_11', 'X_2_12'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2.svg', width=1100, height=650)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_2', 'X_2_4', 'X_2_7', 'X_2_8', 'X_2_9', 'X_2_11', 'X_2_12'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2_redu.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_1', 'X_2_2', 'X_2_3', 'X_2_4', 'X_2_5', 'X_2_6'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2_redu_summer.svg', width=1200, height=600)

In [ ]:
fig1 = px.parallel_coordinates(dt, 
                             dimensions=['alpha',
                                         'X_2_7', 'X_2_8', 'X_2_9', 'X_2_10', 'X_2_11', 'X_2_12'],
                             color="f2", 
                             color_continuous_scale=cm,
                             labels={   'alpha':'λ', 
                                        'f2': 'g<sub>2</sub>',
                                        'X_2_1':'u<sub>1,2</sub>', 
                                        'X_2_2':'u<sub>2,2</sub>', 
                                        'X_2_3':'u<sub>3,2</sub>', 
                                        'X_2_4':'u<sub>4,2</sub>', 
                                        'X_2_5':'u<sub>5,2</sub>', 
                                        'X_2_6':'u<sub>6,2</sub>', 
                                        'X_2_7':'u<sub>7,2</sub>', 
                                        'X_2_8':'u<sub>8,2</sub>', 
                                        'X_2_9':'u<sub>9,2</sub>', 
                                        'X_2_10':'u<sub>10,2</sub>', 
                                        'X_2_11':'u<sub>11,2</sub>', 
                                        'X_2_12':'u<sub>12,2</sub>'},
                             color_continuous_midpoint=2,
                             range_color = [dt.f2.min(), dt.f2.max()])

fig1.show()

#fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2.png', width=1100, height=650)
fig1.write_image('images/fig_mdl2_parallel_coordinates_z2y2_2_redu_winter.svg', width=1200, height=600)